# Quickstart Demo

This showcases the basic operation of Local Neural Descriptor Fields (LNDF)
for a handle grasping task.  

This demonstration loads a set of grasp demos involving some randomly selected
mugs.  We can then use LNDFs to find the handles of other mugs in unique poses
or to grasp handles placed on arbitrary objects.  

If on VScode and the plots don't show, make sure to install the jupyter-notebook-renderers extension.

In [1]:
# Set the absolute base directory path here.
# This is the directory containing lndf_env.sh
lndf_base_dir = '/home/cyc/PycharmProjects/lndf_robot'

import os
import os.path as osp

assert osp.exists(lndf_base_dir), 'Please define lndf_base_dir'

os.environ['LNDF_SOURCE_DIR'] = osp.join(lndf_base_dir, 'src/ndf_robot')
os.environ['PB_PLANNING_SOURCE_DIR'] = osp.join(lndf_base_dir, 'pybullet-planning')

# Set gpu here if you have multiple GPUs
%env CUDA_DEVICE_ORDER=PCI_BUS_ID
%env CUDA_VISIBLE_DEVICES=0

env: CUDA_DEVICE_ORDER=PCI_BUS_ID
env: CUDA_VISIBLE_DEVICES=0


In [2]:
import random
import time

import os.path as osp

from IPython.display import clear_output

import numpy as np
import torch
from torch.nn import functional as F
import trimesh
from trimesh import viewer

from plotly.offline import init_notebook_mode, iplot
import plotly.graph_objects as go

from scipy.spatial.transform import Rotation as R
import plotly.express as px

from ndf_robot.utils import path_util, util, torch_util
from ndf_robot.utils.plotly_save import multiplot

import ndf_robot.model.vnn_occupancy_net.vnn_occupancy_net_pointnet_dgcnn \
    as vnn_occupancy_network
import ndf_robot.model.conv_occupancy_net.conv_occupancy_net \
    as conv_occupancy_network

from ndf_robot.opt.optimizer_lite import OccNetOptimizer

from ndf_robot.eval.query_points import QueryPoints

from ndf_robot.eval.demo_io import DemoIO

seed = 0
init_notebook_mode()
np.random.seed(seed)
random.seed(seed)

pybullet build time: Jan  7 2023 17:38:45


## Set up objects 

We insert an object, convert it to pointcloud, then set it into an upright pose.

We next find a random pose and apply that to the object.

The chart below shows both the upright and rotated object

In [3]:
def make_cut(obj_pcd, r=0.1, sample_pt=None):
    """
    Cut out portion of object that is some distance away from a sample point.

    Args:
        obj_pcd (np.ndarray): (n x 3) array representing a point cloud
        r (float): Radius of cut out.
        sample_pt (np.ndarray, optional): (1 x 3) sample point to cut around. 
            Defaults to None.
    """
    if sample_pt is None:
        sample_pt = obj_pcd[np.random.randint(0, obj_pcd.shape[0])][:]
    print(sample_pt)

    new_pcd = []
    for pt_idx in range(obj_pcd.shape[0]):
        pt = obj_pcd[pt_idx:pt_idx + 1][0]
        dis = (sum((pt.squeeze() - sample_pt)**2))**0.5
        if dis > r:
            new_pcd.append(pt)
    return np.vstack(new_pcd)


In [4]:
use_random_rotation = True
cut_pcd = False 


# -- Some objects to try -- #
obj_model = osp.join(path_util.get_ndf_obj_descriptions(), 'mug_std_centered_obj_normalized/e94e46bc5833f2f5e57b873e4f3ef3a4/models/model_normalized.obj')
# obj_model = osp.join(path_util.get_ndf_obj_descriptions(), 'bowl_handle_std_centered_obj_normalized/34875f8448f98813a2c59a4d90e63212-h/models/model_normalized.obj')
# obj_model = osp.join(path_util.get_ndf_obj_descriptions(), 'bottle_handle_std_centered_obj_normalized/f853ac62bc288e48e56a63d21fb60ae9-h/models/model_normalized.obj')

obj_scale = 1.0
n_samples = 1000
assert osp.exists(obj_model), 'Object model not found'

obj_mesh = trimesh.load(obj_model, process=False)
obj_mesh.apply_scale(obj_scale)
obj_pcd = obj_mesh.sample(n_samples)

upright_rotation = np.eye(4)
upright_rotation[:3, :3] = util.make_rotation_matrix('x', np.pi/2)
obj_pcd = util.transform_pcd(obj_pcd, upright_rotation) 

random_rotation = np.eye(4)
if use_random_rotation:
    random_rotation[:3, :3] = R.random().as_matrix()

rotated_obj_pcd = util.transform_pcd(obj_pcd, random_rotation)

if cut_pcd:
    rotated_obj_pcd = make_cut(rotated_obj_pcd)

fig = multiplot([obj_pcd, rotated_obj_pcd + np.array([[0.2, 0, 0]])], write_html=False) 
fig.update_layout(coloraxis=dict(cmax=2, cmin=-1))
iplot(fig)

# Create Query Points

We feed these query points into the convolutional occupancy network to 
extract our latent activations.

In [5]:
# Choose query points from these types.
QueryPointTypes = {
    'SPHERE',
    'RECT',
    'CYLINDER',
    'ARM',
    'SHELF',
    'NDF_GRIPPER',
    'NDF_RACK',
    'NDF_SHELF',
}

query_pts_type = 'RECT'
query_pts_args = {
    'n_pts': 1000,
    'x': 0.08,
    'y': 0.04,
    'z1': 0.05,
    'z2': 0.02,
}


def create_query_pts(query_pts_type, query_pts_args) -> np.ndarray:
    """
    Create query points from given config

    Args:
        query_pts_config(dict): Configs loaded from yaml file.

    Returns:
        np.ndarray: Query point as ndarray
    """

    assert query_pts_type in QueryPointTypes, 'Invalid query point type'

    if query_pts_type == 'SPHERE':
        query_pts = QueryPoints.generate_sphere(**query_pts_args)
    elif query_pts_type == 'RECT':
        query_pts = QueryPoints.generate_rect(**query_pts_args)
    elif query_pts_type == 'CYLINDER':
        query_pts = QueryPoints.generate_cylinder(**query_pts_args)
    elif query_pts_type == 'ARM':
        query_pts = QueryPoints.generate_rack_arm(**query_pts_args)
    elif query_pts_type == 'SHELF':
        query_pts = QueryPoints.generate_shelf(**query_pts_args)
    elif query_pts_type == 'NDF_GRIPPER':
        query_pts = QueryPoints.generate_ndf_gripper(**query_pts_args)
    elif query_pts_type == 'NDF_RACK':
        query_pts = QueryPoints.generate_ndf_rack(**query_pts_args)
    elif query_pts_type == 'NDF_SHELF':
        query_pts = QueryPoints.generate_ndf_shelf(**query_pts_args)

    return query_pts

query_pts = create_query_pts(query_pts_type, query_pts_args)


fig = multiplot([query_pts, obj_pcd + np.array([[0.2, 0, 0]]), rotated_obj_pcd + np.array([[0.4, 0, 0]])], 
                write_html=False) 
fig.update_layout(coloraxis=dict(cmax=3, cmin=-1))
iplot(fig)

## Create Model 

Define LNDF Model

In [6]:
model_args = {
    'latent_dim': 128,  # Number of voxels in convolutional occupancy network
    'model_type': 'pointnet',  # Encoder type
    'return_features': True,  # Return latent features for evaluation
    'sigmoid': False,  # Use sigmoid activation on last layer
    'acts': 'last',  # Return last activations of occupancy network
}
model_checkpoint = 'lndf_weights.pth'
model_checkpoint_path = osp.join(path_util.get_ndf_model_weights(), model_checkpoint)

model = conv_occupancy_network.ConvolutionalOccupancyNetwork(**model_args)
model.load_state_dict(torch.load(model_checkpoint_path))

<All keys matched successfully>

## Create Pose Optimizer

In [7]:
optimizer_args = {
    'opt_iterations': 500,
    'rand_translate': True,
    'use_tsne': False,
    'M_override': 20,
}

opt_viz_path = 'temp'

optimizer = OccNetOptimizer(model, query_pts, viz_path=opt_viz_path,
                            **optimizer_args)

## Load Demos

In [8]:
demo_exp = 'lndf_mug_handle_demos'
n_demos = 10

demo_load_dir = osp.join(path_util.get_ndf_data(), 'demos', demo_exp)
demo_fnames = os.listdir(demo_load_dir)

assert len(demo_fnames), 'No demonstrations found in path: %s!' \
    % demo_load_dir

# Sort out grasp demos
grasp_demo_fnames = [osp.join(demo_load_dir, fn) for fn in
    demo_fnames if 'grasp_demo' in fn]

demo_shapenet_ids = []
demo_list = []


# Iterate through all demos, extract relevant information and
# prepare to pass into optimizer
random.shuffle(grasp_demo_fnames)
for grasp_demo_fn in grasp_demo_fnames[:n_demos]:
    print('Loading grasp demo from fname: %s' % grasp_demo_fn)
    grasp_data = np.load(grasp_demo_fn, allow_pickle=True)

    demo = DemoIO.process_grasp_data(grasp_data)
    demo_list.append(demo)

    optimizer.add_demo(demo)
    demo_shapenet_ids.append(demo.obj_shapenet_id)

optimizer.process_demos()
clear_output(wait=True)
print('Shapenet IDs used in demo:')
for id in demo_shapenet_ids:
    print('  ' + id)



Shapenet IDs used in demo:
  61c10dccfa8e508e2d66cbf6a91063
  7d6baadd51d0703455da767dfc5b748e
  daee5cf285b8d210eeb8d422649e5f2b
  8f6c86feaa74698d5c91ee20ade72edc
  7a8ea24474846c5c2f23d8349a133d2b
  187859d3c3a2fd23f54e1b6f41fdd78a
  586e67c53f181dc22adf8abaa25e0215
  73b8b6456221f4ea20d3c05c08e26f
  a0c78f254b037f88933dc172307a6bb9
  928a383f79698c3fb6d9bc28c8d8a2c4


## Visualize Demo

The demonstrations consist of an object point cloud, a query point cloud, 
and poses for each that align the query point cloud with a particular part of 
the object point cloud.  We can use these poses to align the object and
query point clouds, which we can then center and use to generate a latent code.

In [9]:
sample_demo = demo_list[0]
demo_obj_pts = sample_demo.obj_pts
# demo_query_pts = sample_demo.query_pts
demo_query_pts = query_pts 
demo_obj_pose = sample_demo.obj_pose_world
demo_query_pose = sample_demo.query_pose_world

posed_obj_pts = util.apply_pose_numpy(demo_obj_pts, demo_obj_pose)
posed_query_pts = util.apply_pose_numpy(demo_query_pts, demo_query_pose)
fig = multiplot([posed_obj_pts, posed_query_pts], write_html=False)
iplot(fig)

## Get Target Pose

We now optimize the latent code of our query points on our test object to 
match the latent codes of our demonstration.  If all goes to plan, this
results in us finding the geometric feature of our test object that most closely
matches those in our demonstrations (e.g. a mug handle).

In [10]:
pose_mats, best_idx, intermediates = optimizer.optimize_transform_implicit(
    rotated_obj_pcd, ee=True, viz_path=opt_viz_path, return_intermediates=True)

[DEBUG][2023-02-24 00:12:30]: i: 99, losses: 0.109668, 0.071540, 0.116874, 0.059845, 0.109330, 0.110524, 0.082418, 0.082438, 0.068016, 0.110820, 0.053163, 0.104012, 0.050459, 0.117677, 0.119155, 0.063132, 0.072700, 0.119343, 0.119126, 0.104153
[DEBUG][2023-02-24 00:12:30]: i: 199, losses: 0.108663, 0.050276, 0.116417, 0.050348, 0.105562, 0.109643, 0.061584, 0.058357, 0.059523, 0.108671, 0.049786, 0.102911, 0.049824, 0.117301, 0.119110, 0.052270, 0.065330, 0.118901, 0.118974, 0.103198
[DEBUG][2023-02-24 00:12:31]: i: 299, losses: 0.108454, 0.049944, 0.091890, 0.049726, 0.103493, 0.109400, 0.050295, 0.050265, 0.049761, 0.104300, 0.049766, 0.102728, 0.049723, 0.117030, 0.119035, 0.052247, 0.057041, 0.118845, 0.118832, 0.103065
[DEBUG][2023-02-24 00:12:31]: i: 399, losses: 0.108454, 0.049726, 0.056145, 0.049725, 0.103082, 0.109327, 0.049744, 0.049741, 0.049742, 0.103232, 0.049746, 0.102784, 0.049723, 0.116953, 0.118960, 0.052296, 0.052258, 0.118807, 0.118689, 0.103090
[DEBUG][2023-02-24 00

## Visualize Target Pose

We can now use the pose found in our previous optimization step for manipulation
of the target object.  In this example, we transform the query points (which
were originally placed at the origin) to the location denoted by the
optimization pose.  The yellow line of dots illustrates the path taken by 
the query points during our optimization procedure.  Note that we initialize
the query points to a random translation within the bounding box of the point
cloud and use LNDFs to refine this into a suitable pose.

In [11]:
idx = best_idx
best_pose_mat = pose_mats[idx]

final_query_pts = util.transform_pcd(query_pts, best_pose_mat)

# Generate trail of intermediate optimization results
intermediate_query_pts = []
query_pts_mean = np.mean(query_pts, axis=0).reshape(1, 3)
for iter_mats in intermediates:
    iter_query_pts = util.transform_pcd(query_pts_mean, iter_mats[idx])
    intermediate_query_pts.append(iter_query_pts)

# Plot all the results
plot_list = [
    rotated_obj_pcd,
    final_query_pts,
] + intermediate_query_pts

plot_pts = np.vstack(plot_list)

# Assign different colors to different objects
color = np.ones(plot_pts.shape[0])
color[rotated_obj_pcd.shape[0]:rotated_obj_pcd.shape[0] + final_query_pts.shape[0]] *= 2
color[rotated_obj_pcd.shape[0] + final_query_pts.shape[0]:] *= 3
fig = px.scatter_3d(
    x=plot_pts[:, 0], y=plot_pts[:, 1], z=plot_pts[:, 2], color=color)
fig.update_layout(coloraxis=dict(cmax=max(color) + 1, cmin=-1))

iplot(fig)

## Next Steps

This demonstration illustrates the main working principles of LNDFs.  For more 
detailed evaluations, see `evaluate_general.py`.  For training details, see 
the `training` directory.  To collect new demos, see the `data_gen` directory.
For more intuition behind our approach, please see our publication in ICRA 2023.